In [59]:
%reset

In [6]:
import numpy as np
import pandas as pd
import tensorflow as tf
meow =['\x07', '\t', '\n', '\x15', '\x1a', '#', '$', '%',
       '(', ')', '*',  '/', '<', '=', '>', '?',
       '@', '[', '\\', ']', '^', '_', '`',  '{', '|', '}', '~', '«', '°',
       '·', '»', '¿', '×', 'ë', 'ı', '̆',
       'ο', 'τ', 'Ё', 'Є', 'Ї', 'Ј', 'ё', 'є', 'і', 'ї', 'ў', 'ү', 'ө', '–',
       '—', '’', '‚', '“', '”', '…', '€', '№', '∙', '√', '│', '┐', '┼',
       '╕', '╜', '╡', '╢', '╦', '▒', '▓']

In [7]:
# book = 'books/all_books1.txt'
book = 'books/dialog_part.txt'
with open(book ,'r',encoding="utf-8") as fp:
    text = fp.read()
start_index = text.find('The START')
end_index = text.find('The END')
text = text[start_index:end_index]
for i in meow:
    text = text.replace(i,' ')
char_set = set(text)
print(f"Общая длина текста книги:{len(text)}")
print(f"Общая длина уникального текста книги:{len(char_set)}")


Общая длина текста книги:113944882
Общая длина уникального текста книги:143


In [8]:
chars_sorted = sorted(char_set)
char2int = {ch:i for i,ch in enumerate(chars_sorted)} #индексируем каждый уникальный символ
# char_array = np.array(chars_sorted)
# char2int

In [9]:
char_array = np.array(chars_sorted)
char_array


array([' ', '!', '"', '&', "'", '+', ',', '-', '.', '0', '1', '2', '3',
       '4', '5', '6', '7', '8', '9', ':', ';', 'A', 'B', 'C', 'D', 'E',
       'F', 'G', 'H', 'I', 'J', 'K', 'L', 'M', 'N', 'O', 'P', 'Q', 'R',
       'S', 'T', 'U', 'V', 'W', 'X', 'Y', 'Z', 'a', 'b', 'c', 'd', 'e',
       'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r',
       's', 't', 'u', 'v', 'w', 'x', 'y', 'z', 'Κ', 'Μ', 'Ο', 'Π', 'Χ',
       'κ', 'А', 'Б', 'В', 'Г', 'Д', 'Е', 'Ж', 'З', 'И', 'Й', 'К', 'Л',
       'М', 'Н', 'О', 'П', 'Р', 'С', 'Т', 'У', 'Ф', 'Х', 'Ц', 'Ч', 'Ш',
       'Щ', 'Ъ', 'Ы', 'Ь', 'Э', 'Ю', 'Я', 'а', 'б', 'в', 'г', 'д', 'е',
       'ж', 'з', 'и', 'й', 'к', 'л', 'м', 'н', 'о', 'п', 'р', 'с', 'т',
       'у', 'ф', 'х', 'ц', 'ч', 'ш', 'щ', 'ъ', 'ы', 'ь', 'э', 'ю', 'я'],
      dtype='<U1')

In [10]:
text_encoded = np.array([char2int[ch] for ch in text]) #кодируем всю книгу
print(f'Размер закодированного текста: {text_encoded.shape}')
print(f'Пример {text[:15]} ==>кодирование==>{text_encoded[:15]}')
print(f"Пример {text_encoded[:15]} ==>декодирование==>{''.join(char_array[text_encoded[:15]])}")



Размер закодированного текста: (113944882,)
Пример The START - Ну  ==>кодирование==>[ 40  54  51   0  39  40  21  38  40   0   7   0  92 130   0]
Пример [ 40  54  51   0  39  40  21  38  40   0   7   0  92 130   0] ==>декодирование==>The START - Ну 


In [11]:
text_encoded[15:21]

array([134, 129, 125,   0,   0,   7])

In [12]:

ds_text_encoded = tf.data.Dataset.from_tensor_slices(text_encoded)
for ex in ds_text_encoded.take(5):
    print(f"{ex.numpy()}->{char_array[ex.numpy()]}")


40->T
54->h
51->e
0-> 
39->S


In [67]:
ds_text_encoded

<TensorSliceDataset element_spec=TensorSpec(shape=(), dtype=tf.int32, name=None)>

In [13]:
seq_lenght =40
chunk_size = seq_lenght + 1
ds_chunks = ds_text_encoded.batch(chunk_size,drop_remainder=True)
def split_input_target(chunk):
    input_seq = chunk[:-1]
    output_seq = chunk[1:]
    return input_seq, output_seq
ds_sequenses = ds_chunks.map(split_input_target)
for example in ds_sequenses.take(7):
    print(repr("".join(char_array[example[0].numpy()])))
    print(repr("".join(char_array[example[1].numpy()])))


'The START - Ну что  - Теперь он овощ. - '
'he START - Ну что  - Теперь он овощ. - Е'
'сть новости     - Ты понимаешь, что они '
'ть новости     - Ты понимаешь, что они и'
'меют в виду  - Думаю, да    - Швы разошл'
'еют в виду  - Думаю, да    - Швы разошли'
'сь  - Нет, но нога очень болит. - Теперь'
'ь  - Нет, но нога очень болит. - Теперь '
'дежурить буду я.    - Все в порядке  - Н'
'ежурить буду я.    - Все в порядке  - Не'
' совсем, но мы целы и невредимы    - И в'
'совсем, но мы целы и невредимы    - И ва'
'м нужно три пары очков  - Будьте так люб'
' нужно три пары очков  - Будьте так любе'


In [69]:
ds_sequenses.take(12)
for example in ds_sequenses.take(17):
    print("".join(char_array[example[0].numpy()[1]]))

h
т
е
ь
е
с
 
н
 
с
д
т




ь
в
я


In [14]:
BUFFER_SIZE = 1000
BATCH_SIZE = 64
ds = ds_sequenses.batch(BATCH_SIZE)
for example in ds.take(7):
    print("".join(char_array[example[0].numpy()[1]]))



сть новости     - Ты понимаешь, что они 
ть в ближайшие двадцать четыре часа  - П
ори, ладно     - Ты уже написал  - Да. -
ет. - Зачем  - Включи!    - Предохраните
рика.    - Почему  - Просто не могу, и в
л - люблю т - тебя, Д - д - джимми!    -
 светлость  - Да, черт бы вас побрал!   


In [75]:
tf.random.set_seed(1)
def build_model(vocab_size:int,embedding_dim:int,rnn_units:str):
    model = tf.keras.Sequential()
    model.add(tf.keras.layers.Embedding(vocab_size,embedding_dim))
    model.add(tf.keras.layers.LSTM(rnn_units,return_sequences=True))
    # model.add(tf.keras.layers.Dense(vocab_size*2))
    # model.add(tf.keras.layers.Dropout(0.3))
    model.add(tf.keras.layers.Dense(vocab_size))
    return model
charset_size = len(char_array)
embedding_dim = 256
rnn_units = 512
model = build_model(vocab_size = charset_size,
                    embedding_dim = embedding_dim,
                    rnn_units = rnn_units)
model.summary()



Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding (Embedding)       (None, None, 256)         54528     
                                                                 
 lstm (LSTM)                 (None, None, 512)         1574912   
                                                                 
 dense (Dense)               (None, None, 213)         109269    
                                                                 
Total params: 1,738,709
Trainable params: 1,738,709
Non-trainable params: 0
_________________________________________________________________


In [ ]:
model.compile(optimizer='adam',loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True))
model.fit(ds,epochs = 20)

Epoch 1/20
17096/43425 [==========>...................] - ETA: 2:59:06 - loss: 1.5470 

KeyboardInterrupt: 

In [71]:
# model.save('books_reader.h5',overwrite=True,
#                 include_optimizer=True,save_format='h5')
#
#

In [15]:
loaded_model=tf.keras.models.load_model('books_reader.h5')
loaded_model.summary()

Model: "sequential_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_1 (Embedding)     (None, None, 256)         51200     
                                                                 
 lstm_1 (LSTM)               (None, None, 512)         1574912   
                                                                 
 dense_1 (Dense)             (None, None, 200)         102600    
                                                                 
Total params: 1,728,712
Trainable params: 1,728,712
Non-trainable params: 0
_________________________________________________________________


In [16]:
loaded_model.fit(ds,epochs=20)

Epoch 1/20
21729/43425 [==============>...............] - ETA: 2:29:39 - loss: 1.5182  


KeyboardInterrupt



In [29]:
def sample(model,starting_str,len_generated_text=100,max_input_length=40,
           scale_factor=1.0):
    encoded_input = [char2int[s] for s in starting_str]
    encoded_input = tf.reshape(encoded_input,(1,-1))
    # print(encoded_input)
    generated_str = starting_str

    model.reset_states()
    for i in range(len_generated_text):
        logits = model(encoded_input)
        logits = tf.squeeze(logits,0) # уменьшает размерность

        scaled_logits = logits * scale_factor
        new_char_indx = tf.random.categorical(scaled_logits,num_samples=1)

        new_char_indx = tf.squeeze(new_char_indx)[-1].numpy()

        generated_str += str(char_array[new_char_indx])
        new_char_indx = tf.expand_dims([new_char_indx],0)

        encoded_input = tf.concat(
            [encoded_input,new_char_indx],
            axis = 1
        )
        encoded_input = encoded_input[:, -max_input_length:]
    return generated_str

print(sample(loaded_model,starting_str='Ситуация просто вопиющая'))



Ситуация просто вопиющая, Камболь, она столь же нужен нам И С. С. Энгб, восприятие разных тексте: над подобной к, левая одно
